# Pełny Cykl Życia Modelu Sentymentu

Ten notebook krok po kroku demonstruje cały cykl życia modelu do klasyfikacji sentymentu, od przygotowania danych, przez eksperymenty i wybór najlepszego modelu, aż po jego użycie do predykcji na nowych danych.

## Sekcja 1: Przygotowanie i Konfiguracja

Zakładamy, że dane treningowe zostały już przygotowane i znajdują się w pliku `artifacts/data/all_train.csv`. W tej komórce definiujemy zmienne, których będziemy używać w całym procesie.

In [1]:
import os
import pandas as pd
import json

os.environ['EXPERIMENT_ID'] = "exp_notebook_tutorial"
os.environ['INPUT_DATA'] = "artifacts/data/all_train.csv"

## Sekcja 2: Generowanie Podziałów Danych

Tworzymy podziały danych dla naszego eksperymentu. Użyjemy strategii `train-val` z wydzielonym zbiorem testowym (20% danych), który posłuży do ostatecznej oceny najlepszego modelu.

In [2]:
!uv run cli generate-splits --experiment-id $EXPERIMENT_ID --input-file $INPUT_DATA --test-size 0.2 --backtesting-strategy train-val

2025-10-29 12:56:43.951 | INFO     | mlops.app:generate_splits:31 - Created directory structure for experiment 'exp_notebook_tutorial'
2025-10-29 12:56:43.970 | INFO     | mlops.app:generate_splits:39 - Saved test set to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/experiments/exp_notebook_tutorial/test.csv
2025-10-29 12:56:43.970 | INFO     | mlops.app:generate_splits:41 - Generating backtesting splits with strategy: 'train-val'...
2025-10-29 12:56:43.981 | INFO     | mlops.app:generate_splits:57 - - Generated train/val/test split in /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/experiments/exp_notebook_tutorial/backtesting/train-val
2025-10-29 12:56:43.981 | INFO     | mlops.app:generate_splits:59 - Generating performance estimation splits...
2025-10-29 12:56:43.992 | INFO     | mlops.app:generate_splits:64 - - Generated train/val split in /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/experiments/exp_notebook_tutorial/performance

## Sekcja 3: Uruchomienie Eksperymentów i Porównanie Modeli

Teraz uruchomimy proces treningu i walidacji dla każdego z wybranych modeli. Po każdym przebiegu wyświetlimy zaktualizowaną tabelę z porównaniem wyników.

### Model: svm-base

In [2]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name svm-base

2025-11-04 20:15:32.042 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-11-04 20:15:32.042 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: SVMModel from models.svm.model
2025-11-04 20:15:32.185 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-11-04 20:15:32.191 | INFO     | models.svm.model:train:39 - Logging configured. Log file: /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_backtesting/fold_0/svm-base/training.log
2025-11-04 20:15:32.191 | INFO     | models.svm.model:train:42 - Creating SVM pipeline...
2025-11-04 20:15:32.191 | INFO     | models.svm.model:train:82 - Training the SVM model with predefined hyperparameters...
2025-11-04 20:15:33.616 | INFO     | models.svm.model:train:88 - Training finished.
2025-11-04 20:15:33.616 | INFO     | models.svm.model:train:91 - Saving model to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_m

In [3]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-11-04 20:19:08.151 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-11-04 20:19:08.152 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-11-04 20:19:08.152 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-11-04 20:19:08.158 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1                  bert-micro-long  0.643162  0.536105  0.643162  0.576582
2                          finbert  0.822650  0.812028  0.822650  0.815154
3     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
4  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
5    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.0

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                   roberta-base-3     0  0.850427   0.859027   
1  backtesting                     roberta-base     0  0.844017   0.850461   
2  backtesting                          finbert     0  0.822650   0.812028   
3  backtesting                          svm-opt     0  0.705128   0.687651   
4  backtesting                         svm-base     0  0.675214   0.669999   
5  backtesting                  bert-micro-long     0  0.643162   0.536105   
6  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
7  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
8  backtesting                  bert-micro-base     0  0.536325   0.287644   
9  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.850427  0.853571  
1  0.844017  0.828156  
2  0.822650  0.815154  
3  0.705128  0.688811  
4  0.675214  0.671415  
5  0.643162  0.576582  
6  0.621795  0.613496  
7  0.606838  0.626360  
8  0.536325  0.374458  
9  0.000000  0.000000

### Model: svm-opt

In [4]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name svm-opt

2025-11-04 20:21:42.430 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-11-04 20:21:42.430 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: SVMModel from models.svm.model
2025-11-04 20:21:42.514 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-11-04 20:21:42.520 | INFO     | models.svm.model:train:39 - Logging configured. Log file: /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_backtesting/fold_0/svm-opt/training.log
2025-11-04 20:21:42.520 | INFO     | models.svm.model:train:42 - Creating SVM pipeline...
2025-11-04 20:21:42.521 | INFO     | models.svm.model:train:54 - Validation dataset provided and hyperparameter_search config found, performing randomized search...
[CV] END .......clf__C=0.1, clf__gamma=auto, clf__kernel=rbf; total time=   0.9s
[CV] END .......clf__C=0.1, clf__gamma=auto, clf__kernel=rbf; total time=   1.0s
[CV] END ...clf__C=0.1, clf__gamma=

In [5]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-11-04 20:22:15.897 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-11-04 20:22:15.897 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-11-04 20:22:15.897 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-11-04 20:22:15.902 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1                  bert-micro-long  0.643162  0.536105  0.643162  0.576582
2                          finbert  0.822650  0.812028  0.822650  0.815154
3     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
4  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
5    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.0

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                   roberta-base-3     0  0.850427   0.859027   
1  backtesting                     roberta-base     0  0.844017   0.850461   
2  backtesting                          finbert     0  0.822650   0.812028   
3  backtesting                          svm-opt     0  0.705128   0.687651   
4  backtesting                         svm-base     0  0.675214   0.669999   
5  backtesting                  bert-micro-long     0  0.643162   0.536105   
6  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
7  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
8  backtesting                  bert-micro-base     0  0.536325   0.287644   
9  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.850427  0.853571  
1  0.844017  0.828156  
2  0.822650  0.815154  
3  0.705128  0.688811  
4  0.675214  0.671415  
5  0.643162  0.576582  
6  0.621795  0.613496  
7  0.606838  0.626360  
8  0.536325  0.374458  
9  0.000000  0.000000

### Model: Gemma Zero-shot

In [7]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name prompt-gemma-zeroshot-3-1b-it

2025-10-29 12:57:13.395 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 12:57:13.395 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: PromptGemmaModel from models.prompt_gemma.model
2025-10-29 12:57:13.412 | INFO     | models.prompt_gemma.model:__init__:23 - Using device: mps
2025-10-29 12:57:13.412 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 12:57:13.412 | INFO     | models.prompt_gemma.model:train:39 - PromptGemmaModel does not require training. Skipping.
2025-10-29 12:57:13.412 | INFO     | models.prompt_gemma.model:train:52 - Output directory ensured at: /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_backtesting/fold_0/prompt-gemma-zeroshot-3-1b-it
2025-10-29 12:57:13.413 | INFO     | mlops.runner:_save_model_spec:47 - Model spec saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_ba

### Model: Gemma Few-shot

In [8]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name prompt-gemma-fewshot-3-1b-it

2025-10-29 12:59:25.816 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 12:59:25.816 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: PromptGemmaModel from models.prompt_gemma.model
2025-10-29 12:59:25.830 | INFO     | models.prompt_gemma.model:__init__:23 - Using device: mps
2025-10-29 12:59:25.830 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 12:59:25.830 | INFO     | models.prompt_gemma.model:train:39 - PromptGemmaModel does not require training. Skipping.
2025-10-29 12:59:25.830 | INFO     | models.prompt_gemma.model:train:52 - Output directory ensured at: /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_backtesting/fold_0/prompt-gemma-fewshot-3-1b-it
2025-10-29 12:59:25.831 | INFO     | mlops.runner:_save_model_spec:47 - Model spec saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_bac

In [9]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 13:03:30.187 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 13:03:30.188 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 13:03:30.189 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 13:03:30.195 | INFO     | evaluate:compare_models:95 - 
                      model_name  accuracy precision    recall  f1_score
                                      mean      mean      mean      mean
0   prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
1  prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
2                       svm-base  0.675214  0.669999  0.675214  0.671415
3                        svm-opt  0.705128  0.687651  0.705128  0.688811
2025-10-29 13:03:30.196 | INFO     | evaluate:compare_models:100 - Comparison report saved to artifacts/experiments/exp_notebook_tutorial/comparison.csv


run_type                     model_name  fold  accuracy  precision  \
0  backtesting                        svm-opt     0  0.705128   0.687651   
1  backtesting                       svm-base     0  0.675214   0.669999   
2  backtesting   prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
3  backtesting  prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.705128  0.688811  
1  0.675214  0.671415  
2  0.606838  0.626360  
3  0.000000  0.000000

### Model: Gemma Few-shot v2

In [10]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name prompt-gemma-fewshot-v2-3-1b-it

2025-10-29 13:03:33.942 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 13:03:33.942 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: PromptGemmaModel from models.prompt_gemma.model
2025-10-29 13:03:33.957 | INFO     | models.prompt_gemma.model:__init__:23 - Using device: mps
2025-10-29 13:03:33.957 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 13:03:33.957 | INFO     | models.prompt_gemma.model:train:39 - PromptGemmaModel does not require training. Skipping.
2025-10-29 13:03:33.957 | INFO     | models.prompt_gemma.model:train:52 - Output directory ensured at: /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_backtesting/fold_0/prompt-gemma-fewshot-v2-3-1b-it
2025-10-29 13:03:33.958 | INFO     | mlops.runner:_save_model_spec:47 - Model spec saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/trained_models/exp_notebook_tutorial_

In [11]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 13:08:59.652 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 13:08:59.653 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 13:08:59.653 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 13:08:59.656 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
1  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
2    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
3                         svm-base  0.675214  0.669999  0.675214  0.671415
4                          svm-opt  0.705128  0.687651  0.705128  0.688811
2025-10-29 13:08:59.658 | INFO     | evaluate:compare_models:100 - Co

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                          svm-opt     0  0.705128   0.687651   
1  backtesting                         svm-base     0  0.675214   0.669999   
2  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
3  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
4  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.705128  0.688811  
1  0.675214  0.671415  
2  0.621795  0.613496  
3  0.606838  0.626360  
4  0.000000  0.000000

### Model: bert-micro-base

In [12]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name bert-micro-base

2025-10-29 13:09:03.419 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 13:09:03.419 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-29 13:09:07.892 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 13:09:07.892 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|█████████████████████████| 3504/3504 [00:00<00:00, 8982.98 examples/s]
2025-10-29 13:09:08.699 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|███████████████████████████| 701/701 [00:00<00:00, 9777.13 examples/s]
2025-10-29 13:09:08.777 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-29 13:09:08.778 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-29 13:09:08.778 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...


In [13]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 13:10:48.687 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 13:10:48.687 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 13:10:48.687 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 13:10:48.691 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
2  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
3    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
4                         svm-base  0.675214  0.669999  0.675214  0.671415
5                          svm-opt  0.705128  0.687651  0.705128  0.6

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                          svm-opt     0  0.705128   0.687651   
1  backtesting                         svm-base     0  0.675214   0.669999   
2  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
3  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
4  backtesting                  bert-micro-base     0  0.536325   0.287644   
5  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.705128  0.688811  
1  0.675214  0.671415  
2  0.621795  0.613496  
3  0.606838  0.626360  
4  0.536325  0.374458  
5  0.000000  0.000000

### Model: bert-micro-long

In [14]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name bert-micro-long

2025-10-29 13:10:52.304 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 13:10:52.304 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-29 13:10:55.709 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 13:10:55.709 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|█████████████████████████| 3504/3504 [00:00<00:00, 9139.90 examples/s]
2025-10-29 13:10:56.496 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|███████████████████████████| 701/701 [00:00<00:00, 9324.31 examples/s]
2025-10-29 13:10:56.578 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-29 13:10:56.578 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-29 13:10:56.579 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...


In [15]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 13:18:36.989 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 13:18:36.990 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 13:18:36.990 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 13:18:36.993 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1                  bert-micro-long  0.643162  0.536105  0.643162  0.576582
2     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
3  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
4    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
5                         svm-base  0.675214  0.669999  0.675214  0.6

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                          svm-opt     0  0.705128   0.687651   
1  backtesting                         svm-base     0  0.675214   0.669999   
2  backtesting                  bert-micro-long     0  0.643162   0.536105   
3  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
4  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
5  backtesting                  bert-micro-base     0  0.536325   0.287644   
6  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.705128  0.688811  
1  0.675214  0.671415  
2  0.643162  0.576582  
3  0.621795  0.613496  
4  0.606838  0.626360  
5  0.536325  0.374458  
6  0.000000  0.000000

### Model: roberta-base

In [16]:
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name roberta-base

2025-10-29 13:18:40.579 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 13:18:40.579 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-29 13:18:44.016 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 13:18:44.017 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|████████████████████████| 3504/3504 [00:00<00:00, 11571.20 examples/s]
2025-10-29 13:18:44.983 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|██████████████████████████| 701/701 [00:00<00:00, 12395.69 examples/s]
2025-10-29 13:18:45.060 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-29 13:18:45.060 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-29 13:18:45.060 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...


In [17]:
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 13:44:52.709 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 13:44:52.709 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 13:44:52.709 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 13:44:52.713 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1                  bert-micro-long  0.643162  0.536105  0.643162  0.576582
2     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
3  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
4    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
5                     roberta-base  0.844017  0.850461  0.844017  0.8

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                     roberta-base     0  0.844017   0.850461   
1  backtesting                          svm-opt     0  0.705128   0.687651   
2  backtesting                         svm-base     0  0.675214   0.669999   
3  backtesting                  bert-micro-long     0  0.643162   0.536105   
4  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
5  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
6  backtesting                  bert-micro-base     0  0.536325   0.287644   
7  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.844017  0.828156  
1  0.705128  0.688811  
2  0.675214  0.671415  
3  0.643162  0.576582  
4  0.621795  0.613496  
5  0.606838  0.626360  
6  0.536325  0.374458  
7  0.000000  0.000000

### Eksperyment: Zwiększenie liczby epok dla `roberta-base`

Tworzymy nową konfigurację `roberta-base-3` w locie, zmieniając liczbę epok treningowych, aby sprawdzić, czy dłuższy trening poprawi wynik.

In [18]:
# Wczytanie bazowej konfiguracji
with open('model_configs/roberta-base.json', 'r') as f:
    config = json.load(f)

# Modyfikacja hiperparametru
config["training_arguments"]["num_train_epochs"] = 3

# Zapis nowej konfiguracji
with open('model_configs/roberta-base-3.json', 'w') as f:
    json.dump(config, f, indent=4)

print("Utworzono nową konfigurację: model_configs/roberta-base-3.json")

Utworzono nową konfigurację: model_configs/roberta-base-3.json


In [19]:
# Uruchomienie eksperymentu dla nowej konfiguracji
!uv run cli run-backtesting --experiment-id $EXPERIMENT_ID --model-config-name roberta-base-3

2025-10-29 13:44:56.379 | INFO     | mlops.runner:run_backtesting:58 - --- Backtesting Fold 0 ---
2025-10-29 13:44:56.379 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-29 13:45:00.429 | INFO     | mlops.runner:run_backtesting:68 - Training model...
2025-10-29 13:45:00.429 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|████████████████████████| 3504/3504 [00:00<00:00, 11285.38 examples/s]
2025-10-29 13:45:01.359 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|██████████████████████████| 701/701 [00:00<00:00, 12308.40 examples/s]
2025-10-29 13:45:01.436 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-29 13:45:01.436 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-29 13:45:01.436 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...


In [20]:
# Ostateczne porównanie
!uv run cli compare-models --experiment-id $EXPERIMENT_ID --output-file artifacts/experiments/$EXPERIMENT_ID/comparison.csv --run-type backtesting
comparison_df = pd.read_csv(f"artifacts/experiments/{os.environ['EXPERIMENT_ID']}/comparison.csv")
display(comparison_df)

2025-10-29 15:01:00.423 | INFO     | evaluate:compare_models:79 - --- Model Comparison for Experiment 'exp_notebook_tutorial' ---
2025-10-29 15:01:00.424 | INFO     | evaluate:compare_models:82 - 
--- Run Type: backtesting ---
2025-10-29 15:01:00.425 | INFO     | evaluate:compare_models:91 - Summary for backtesting (train-val strategy):
2025-10-29 15:01:00.431 | INFO     | evaluate:compare_models:95 - 
                        model_name  accuracy precision    recall  f1_score
                                        mean      mean      mean      mean
0                  bert-micro-base  0.536325  0.287644  0.536325  0.374458
1                  bert-micro-long  0.643162  0.536105  0.643162  0.576582
2     prompt-gemma-fewshot-3-1b-it  0.606838  0.727688  0.606838  0.626360
3  prompt-gemma-fewshot-v2-3-1b-it  0.621795  0.706001  0.621795  0.613496
4    prompt-gemma-zeroshot-3-1b-it  0.000000  0.000000  0.000000  0.000000
5                     roberta-base  0.844017  0.850461  0.844017  0.8

run_type                       model_name  fold  accuracy  precision  \
0  backtesting                   roberta-base-3     0  0.850427   0.859027   
1  backtesting                     roberta-base     0  0.844017   0.850461   
2  backtesting                          svm-opt     0  0.705128   0.687651   
3  backtesting                         svm-base     0  0.675214   0.669999   
4  backtesting                  bert-micro-long     0  0.643162   0.536105   
5  backtesting  prompt-gemma-fewshot-v2-3-1b-it     0  0.621795   0.706001   
6  backtesting     prompt-gemma-fewshot-3-1b-it     0  0.606838   0.727688   
7  backtesting                  bert-micro-base     0  0.536325   0.287644   
8  backtesting    prompt-gemma-zeroshot-3-1b-it     0  0.000000   0.000000   

     recall  f1_score  
0  0.850427  0.853571  
1  0.844017  0.828156  
2  0.705128  0.688811  
3  0.675214  0.671415  
4  0.643162  0.576582  
5  0.621795  0.613496  
6  0.606838  0.626360  
7  0.536325  0.374458  
8  0.000000  0.000000

## Sekcja 4: Wybór Najlepszego Modelu

Na podstawie powyższych wyników, jako najlepszy model do dalszych kroków wybieramy `roberta-base-3` (założenie na potrzeby tego tutoriala).

In [21]:
os.environ['BEST_MODEL'] = "roberta-base-3"

## Sekcja 5: Oszacowanie Wydajności na Zbiorze Testowym

Wybrany model sprawdzamy na odłożonym wcześniej zbiorze testowym. To da nam ostateczną, bezstronną ocenę jego jakości.

In [22]:
!uv run cli estimate-performance --experiment-id $EXPERIMENT_ID --model-config-name $BEST_MODEL

2025-10-30 10:47:20.878 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-30 10:47:26.833 | INFO     | mlops.runner:run_performance_estimation:105 - Training model for performance estimation...
2025-10-30 10:47:26.833 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|█████████████████████████| 4205/4205 [00:00<00:00, 9097.67 examples/s]
2025-10-30 10:47:27.990 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|███████████████████████████| 468/468 [00:00<00:00, 8308.01 examples/s]
2025-10-30 10:47:28.072 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-30 10:47:28.072 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-30 10:47:28.072 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...
Some weights of RobertaForSequenceClassification were not i

## Sekcja 6: Trening Finalnego Modelu

Mając pewność co do jakości naszego modelu, trenujemy go po raz ostatni na pełnym zbiorze danych (trening + walidacja), aby był gotowy do użycia produkcyjnego.

In [23]:
!uv run cli train-final-model --experiment-id $EXPERIMENT_ID --model-config-name $BEST_MODEL --model-output-dir artifacts/trained_models/

2025-10-30 12:45:24.432 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-30 12:45:28.974 | INFO     | mlops.runner:train_final_model:139 - Training final model...
2025-10-30 12:45:28.974 | INFO     | models.roberta.pipeline:run:15 - Preprocessing data for RoBERTa model...
Map: 100%|████████████████████████| 5257/5257 [00:00<00:00, 12049.57 examples/s]
2025-10-30 12:45:30.076 | INFO     | models.roberta.pipeline:run:41 - Preprocessing validation data...
Map: 100%|██████████████████████████| 585/585 [00:00<00:00, 12181.24 examples/s]
2025-10-30 12:45:30.145 | INFO     | models.roberta.pipeline:run:48 - Validation data preprocessing complete.
2025-10-30 12:45:30.145 | INFO     | models.roberta.pipeline:run:53 - Data preprocessing complete.
2025-10-30 12:45:30.146 | INFO     | models.roberta.pipeline:run:58 - Training RoBERTa model...
Some weights of RobertaForSequenceClassification were not initialized from the model chec

## Sekcja 7: Predykcja na Nowych Danych

Symulujemy scenariusz produkcyjny: pojawiły się nowe dane i chcemy poznać ich sentyment. Użyjemy do tego naszego generatora danych.

In [24]:
import glob
import os

# Run data generation
!uv run cli data-generate --name new_unseen_data --examples-per-sentiment 5

# Find the latest generated file
list_of_dirs = glob.glob('artifacts/new_data/*')
latest_dir = max(list_of_dirs, key=os.path.getctime)
new_data_file = os.path.join(latest_dir, 'new_unseen_data.csv')
os.environ['NEW_DATA_FILE'] = new_data_file
print(f"New data file: {new_data_file}")

2025-10-30 14:30:08.961 | INFO     | data.generator:__init__:15 - Initializing generator with model: google/gemma-3-1b-it
2025-10-30 14:30:15.765 | INFO     | data.generator:__init__:25 - Model and tokenizer loaded successfully.
2025-10-30 14:30:15.765 | INFO     | data.generator:generate:103 - Generating 5 examples for sentiment: 'positive' in language: en
2025-10-30 14:30:20.888 | INFO     | data.generator:generate:107 - (1/5) Generated for 'positive': 486356789000000000000000000000000000000000000000000000000000
2025-10-30 14:30:25.279 | INFO     | data.generator:generate:107 - (2/5) Generated for 'positive': 1000% profit on a new stock, the potential is immense.
2025-10-30 14:30:29.181 | INFO     | data.generator:generate:107 - (3/5) Generated for 'positive': Sentiment: positive
2025-10-30 14:30:34.113 | INFO     | data.generator:generate:107 - (4/5) Generated for 'positive': 10% of Apple is currently being traded at a premium to its earnings of USD 10 billion.
2025-10-30 14:30:37.7

Używamy naszego finalnego modelu do wykonania predykcji na nowych danych.

In [25]:
from pathlib import Path

FINAL_MODEL_PATH = f"artifacts/trained_models/{os.environ['EXPERIMENT_ID']}_final/{os.environ['BEST_MODEL']}"
PREDICTION_ID = "tutorial_prediction" # Using a fixed ID for reproducibility

# Construct the output path based on the new structure
new_data_path = Path(os.environ['NEW_DATA_FILE'])
timestamp = new_data_path.parent.name
name = new_data_path.stem
model_id = os.environ['BEST_MODEL']

PREDICTION_OUTPUT_FILE = f"artifacts/predictions/new_data/{timestamp}/{name}/{model_id}/{PREDICTION_ID}/predictions.csv"

In [27]:
# Using f-string to pass Python variables to the shell command
!uv run cli predict-new --model-path {FINAL_MODEL_PATH} --input-file {os.environ['NEW_DATA_FILE']} --prediction-id {PREDICTION_ID}

2025-10-30 14:32:06.577 | INFO     | mlops.runner:_load_model_from_config:28 - Loading model: RobertaModel from models.roberta.model
2025-10-30 14:32:09.827 | INFO     | models.roberta.pipeline:run:120 - Running RoBERTa predictions...
2025-10-30 14:32:11.730 | INFO     | models.roberta.pipeline:run:152 - Predictions saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/predictions/new_data/20251030_1431/new_unseen_data/roberta-base-3/tutorial_prediction/predictions.csv
2025-10-30 14:32:11.738 | SUCCESS  | mlops.runner:predict_new:172 - Predictions saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/predictions/new_data/20251030_1431/new_unseen_data/roberta-base-3/tutorial_prediction/predictions.csv


In [28]:

# Wyświetlenie predykcji
predictions_df = pd.read_csv(PREDICTION_OUTPUT_FILE)
print("Wygenerowane predykcje:")
display(predictions_df)

Wygenerowane predykcje:


Sentence Sentiment  \
0   4863567890000000000000000000000000000000000000...  positive   
1   1000% profit on a new stock, the potential is ...  positive   
2                                 Sentiment: positive  positive   
3   10% of Apple is currently being traded at a pr...  positive   
4   The stock market experienced a dramatic declin...  positive   
5    100,000 is the projected growth of the IPO in Q3   neutral   
6   The market's recent decline resulted in a sign...   neutral   
7                  123456789 is a valid email address   neutral   
8   The Company's Q3 earnings report showed a sign...   neutral   
9                                 Sentiment: negative  negative   
10  The stock market experienced a significant reb...  negative   
11  99.5% of the market seems optimistic about the...  negative   
12  The volatility of the cryptocurrency market co...  negative   
13  1000 shares of Acme Corp at EUR 10.00 per shar...  negative   

   Predicted_Sentiment  
0              neutral  
1             positive  
2             positive  
3             positive  
4             negative  
5             positive  
6             negative  
7              neutral  
8             positive  
9             negative  
10            positive  
11            positive  
12            negative  
13            positive

## Sekcja 8: Symulacja Oceny Jakości

W realnym scenariuszu dla nowo wygenerowanych danych nie mielibyśmy prawdziwych etykiet. Aby jednak zademonstrować działanie skryptu `evaluate.py`, zasymulujemy ocenę, traktując sentyment, o który prosiliśmy generator, jako "prawdziwą etykietę".

In [29]:
os.environ["NEW_DATA_FILE"]

'artifacts/new_data/20251030_1431/new_unseen_data.csv'

In [32]:
!uv run cli evaluate-prediction --predictions-file {PREDICTION_OUTPUT_FILE} --ground-truth-file {os.environ['NEW_DATA_FILE']} --display

2025-10-30 14:35:51.189 | INFO     | mlops.app:evaluate_prediction:86 - Evaluating predictions from 'artifacts/predictions/new_data/20251030_1431/new_unseen_data/roberta-base-3/tutorial_prediction/predictions.csv' against 'artifacts/new_data/20251030_1431/new_unseen_data.csv'.
2025-10-30 14:35:51.193 | INFO     | mlops.app:evaluate_prediction:88 - Evaluation metrics: {'accuracy': 0.42857142857142855, 'precision': 0.45535714285714285, 'recall': 0.42857142857142855, 'f1_score': 0.4188034188034188}
2025-10-30 14:35:51.194 | SUCCESS  | mlops.app:evaluate_prediction:96 - Metrics saved to /Users/witjakuczunpriv/projects/AI_MasterClass_CIONET/artifacts/metrics/20251030_1431/new_unseen_data/roberta-base-3/metrics.csv
   accuracy  precision    recall  f1_score
0  0.428571   0.455357  0.428571  0.418803
